In [22]:
import pandas as pd
import altair as alt
import requests
import math
import numpy as np

In [2]:
df = pd.read_csv("../data/sbdb_query_results.csv")
df.head()
df = df.rename(columns={
    'per_y': 'P (yr)',
    'moid': 'MOID (AU)',
    'q': 'q (AU)',
    'e': 'e',
    'i': 'i (deg)',
    'epoch_cal': 'Epoch',
    'a': 'Semi-major Axis'
})
df = df[df["P (yr)"] < 25]
df

full_name     ad        tp_cal       e  q (AU)  \
1                       2P/Encke   4.10  2023-10-21.7  0.8483   0.337   
2                       3D/Biela   6.19  1832-11-26.6  0.7513   0.879   
3                        4P/Faye   6.02  2021-09-05.6  0.5845   1.578   
4                     5D/Brorsen   5.61  1879-03-31.0  0.8098   0.590   
5                    6P/d'Arrest   5.64  2021-09-17.7  0.6127   1.355   
...                          ...    ...           ...     ...     ...   
3986          P/2024 T2 (Rankin)  10.38  2024-12-08.3  0.6807   1.972   
3995       P/2024 X3 (PANSTARRS)  11.38  2024-09-05.7  0.6263   2.614   
3999       P/2025 A2 (PANSTARRS)   6.73  2024-10-05.6  0.3224   3.446   
4005           P/2025 C1 (ATLAS)   5.64  2025-02-06.5  0.3454   2.746   
4008       P/2025 D3 (PANSTARRS)   4.97  2024-07-25.6  0.2524   2.965   

      i (deg)      om       w  P (yr) class  ...            A3    DT  \
1       11.47  334.27  187.05    3.31   ETc  ...           NaN   NaN   
2       13.22  250.67  221.66    6.65   JFc  ...           NaN   NaN   
3        8.16  194.80  205.99    7.40   JFc  ... -7.100000e-10 -37.7   
4       29.38  102.97   14.95    5.46   JFc  ...           NaN   NaN   
5       19.51  138.94  178.11    6.54   JFc  ...           NaN   NaN   
...       ...     ...     ...     ...   ...  ...           ...   ...   
3986    12.93  113.06  343.83   15.30   JFc  ...           NaN   NaN   
3995     2.97  113.36  352.94   18.50   JFc  ...           NaN   NaN   
3999    20.73  189.32  278.03   11.50   JFc  ...           NaN   NaN   
4005     7.52    9.10  186.79    8.59   JFc  ...           NaN   NaN   
4008     9.64  186.64  294.45    7.90   JFc  ...           NaN   NaN   

           name      epoch         Epoch  Semi-major Axis  MOID (AU)  moid_ld  \
1         Encke  2459780.5  2022-07-20.0            2.220   0.168000   65.300   
2         Biela  2390520.5  1832-12-03.0            3.535   0.000518    0.202   
3          Faye  2458522.5  2019-02-08.0            3.798   0.589000  229.000   
4       Brorsen  2407440.5  1879-04-01.0            3.101   0.367000  143.000   
5      d'Arrest  2459302.5  2021-03-29.0            3.497   0.343000  133.000   
...         ...        ...           ...              ...        ...      ...   
3986     Rankin  2460691.5  2025-01-16.0            6.176   0.992000  386.000   
3995  PANSTARRS  2460703.5  2025-01-28.0            6.995   1.630000  635.000   
3999  PANSTARRS  2460697.5  2025-01-22.0            5.086   2.550000  992.000   
4005      ATLAS  2460731.5  2025-02-25.0            4.195   1.750000  679.000   
4008  PANSTARRS  2460730.5  2025-02-24.0            3.967   2.000000  778.000   

       first_obs    last_obs  
1     2018-11-05  2025-06-29  
2            NaN         NaN  
3     2013-05-23  2023-03-25  
4            NaN         NaN  
5     2014-03-10  2022-03-01  
...          ...         ...  
3986  2024-10-04  2025-05-02  
3995  2024-10-22  2025-05-18  
3999  2024-11-27  2025-04-02  
4005  2025-02-02  2025-06-12  
4008  2024-12-30  2025-04-02  

[839 rows x 26 columns]

In [3]:
df = df[
    df['P (yr)'].notna() &
    df['e'].notna() &
    df['i (deg)'].notna() &
    df['q (AU)'].notna() &
    df['MOID (AU)'].notna() &
    df['Semi-major Axis'].notna()
    ]

df['Epoch'] = pd.to_datetime(df['Epoch'].str.replace('.0', '', regex=False), format='%Y-%m-%d', errors='coerce')
df = df[df['Epoch'].notna()]
df['Decade'] = (df['Epoch'].dt.year // 10) * 10
df['Period Class'] = df['P (yr)'].apply(lambda x: 'Short (<20yr)' if x < 20 else 'Long (≥20yr)')


/var/folders/bb/3_ttlmmn3gj0nwmdbrszt_rr0000gn/T/ipykernel_88407/786609737.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Epoch'] = pd.to_datetime(df['Epoch'].str.replace('.0', '', regex=False), format='%Y-%m-%d', errors='coerce')


In [4]:
alt.Chart(df).mark_circle(opacity=0.6).encode(
    x=alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
    y=alt.Y('P (yr):Q', title='Orbital Period (yrs)', scale=alt.Scale(type='log')),
    color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='redblue')),
    size=alt.Size('MOID (AU):Q', title='Distance from Earth (AU)', scale=alt.Scale(range=[10, 500], reverse=True)),
    tooltip=[
        alt.Tooltip('full_name:N', title='Comet:'),
        alt.Tooltip('Epoch:T', title='Date Discovered:'),
        alt.Tooltip('P (yr):Q', title='Period (yr):'),
        alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
        alt.Tooltip('e:Q', title='Eccentricity:'),
        alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
    ]
).properties(
    title="Comet Orbital Period vs Perihelion Distance",
    width=600,
    height=400
)

alt.Chart(...)

In [5]:
df = df[df["Decade"] > 1960]

In [6]:
#bind = alt.selection_interval(bind='scales', encodings=["x"])
selection = alt.selection_interval()

alt.Chart(df).mark_circle(opacity=0.6).add_params(
    #bind,
    selection
).encode(
    x=alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
    y=alt.Y('P (yr):Q', title='Orbital Period (yrs)'), #scale=alt.Scale(type='log')),
    color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='redblue')),
    size=alt.Size('MOID (AU):Q', title='Distance from Earth (AU)', scale=alt.Scale(range=[10, 500], reverse=True)),
    tooltip=[
        alt.Tooltip('full_name:N', title='Comet:'),
        alt.Tooltip('Epoch:T', title='Date Discovered:'),
        alt.Tooltip('P (yr):Q', title='Period (yr):'),
        alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
        alt.Tooltip('e:Q', title='Eccentricity:'),
        alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
    ]
).properties(
    title="Comet Orbital Period vs Perihelion Distance",
    width=600,
    height=400
)

alt.Chart(...)

In [7]:
#bind = alt.selection_interval(bind='scales', encodings=["x"])
selection = alt.selection_interval()

alt.Chart(df).mark_circle(opacity=0.6).add_params(
    #bind,
    selection
).encode(
    x = alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
    y = alt.Y('P (yr):Q', title='Orbital Period (yrs)'), #scale=alt.Scale(type='log')),
    color = alt.condition(selection, "e:Q", alt.value("lightgray"), scale = alt.Scale(scheme="viridis"), title="Eccentricity"),
    size = alt.Size('MOID (AU):Q', title='Distance from Earth (AU)', scale=alt.Scale(range=[10, 500], reverse=True)),
    tooltip = [
        alt.Tooltip('full_name:N', title='Comet:'),
        alt.Tooltip('Epoch:T', title='Date Discovered:'),
        alt.Tooltip('P (yr):Q', title='Period (yr):'),
        alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
        alt.Tooltip('e:Q', title='Eccentricity:'),
        alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
    ]
).properties(
    title="What characteristics of Near Earth Comets affect its orbital period?",
    width=600,
    height=400
)

alt.Chart(...)

In [8]:
selection = alt.selection_interval()
dropdown = alt.binding_select(options=sorted(df["Decade"].unique()), name="Decade:")
decade_select = alt.selection_point(fields=['Decade'], bind=dropdown)

alt.Chart(df).mark_circle(opacity=0.6).add_params(
    selection,
    decade_select
).transform_filter(
    decade_select
).encode(
    x = alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
    y = alt.Y('P (yr):Q', title='Orbital Period (yrs)'), #scale=alt.Scale(type='log')),
    color = alt.condition(selection, "e:Q", alt.value("lightgray"), scale = alt.Scale(scheme="viridis"), title="Eccentricity"),
    size = alt.Size('MOID (AU):Q', title='Distance from Earth (AU)', scale=alt.Scale(range=[10, 500], reverse=True)),
    tooltip = [
        alt.Tooltip('full_name:N', title='Comet:'),
        alt.Tooltip('Epoch:T', title='Date Discovered:'),
        alt.Tooltip('P (yr):Q', title='Period (yr):'),
        alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
        alt.Tooltip('e:Q', title='Eccentricity:'),
        alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
    ]
).properties(
    title="What characteristics of Near Earth Comets affect its orbital period?",
    width=600,
    height=400
)

alt.Chart(...)

In [9]:
selection = alt.selection_interval()
dropdown = alt.binding_select(options=sorted(df["Decade"].unique()), name="Decade:")
decade_select = alt.selection_point(fields=['Decade'], bind=dropdown)

alt.Chart(df).mark_point(opacity=0.6).add_params(
    selection,
    decade_select
).transform_filter(
    decade_select
).encode(
    x = alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
    y = alt.Y('P (yr):Q', title='Orbital Period (yrs)'), #scale=alt.Scale(type='log')),
    color = alt.condition(selection, "e:Q", alt.value("lightgray"), scale = alt.Scale(scheme="viridis"), title="Eccentricity"),
    #size = alt.Size('MOID (AU):Q', title='Distance from Earth (AU)', scale=alt.Scale(range=[10, 500], reverse=True)),
    tooltip = [
        alt.Tooltip('full_name:N', title='Comet:'),
        alt.Tooltip('Epoch:T', title='Date Discovered:'),
        alt.Tooltip('P (yr):Q', title='Period (yr):'),
        alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
        alt.Tooltip('e:Q', title='Eccentricity:'),
        alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
    ]
).properties(
    title="What characteristics of Near Earth Comets affect its orbital period?",
    width=600,
    height=400
)

alt.Chart(...)

In [10]:
selection = alt.selection_interval()
dropdown = alt.binding_select(options=sorted(df["Decade"].unique()), name="Decade:")
decade_select = alt.selection_point(fields=['Decade'], bind=dropdown)

alt.Chart(df).mark_point(
    opacity=0.6,
    strokeWidth=1.25,
    filled=True
).add_params(
    selection,
    decade_select
).transform_filter(
    decade_select
).encode(
    x = alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
    y = alt.Y('P (yr):Q', title='Orbital Period (yrs)'), #scale=alt.Scale(type='log')),
    yOffset='jitter:Q',
    color = alt.condition(selection, "e:Q", alt.value("lightgray"), scale = alt.Scale(scheme="viridis"), title="Eccentricity"),
    #size = alt.Size('MOID (AU):Q', title='Distance from Earth (AU)', scale=alt.Scale(range=[10, 500], reverse=True)),
    tooltip = [
        alt.Tooltip('full_name:N', title='Comet:'),
        alt.Tooltip('Epoch:T', title='Date Discovered:'),
        alt.Tooltip('P (yr):Q', title='Period (yr):'),
        alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
        alt.Tooltip('e:Q', title='Eccentricity:'),
        alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
    ]
).transform_calculate(
    # Generate Gaussian jitter
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).properties(
    title="What characteristics of Near Earth Comets affect its orbital period?",
    width=600,
    height=400
)

alt.Chart(...)

In [11]:
brush = alt.selection_interval(encodings=['x'])

dropdown = alt.binding_select(options=sorted(df["Decade"].unique()), name="Decade:")
decade_select = alt.selection_point(fields=['Decade'], bind=dropdown)

base = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter(decade_select)
      .transform_calculate(
          # Gaussian jitter to reduce overlap (requires Altair 5)
          jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
      )
)

points = (
    base.mark_point(opacity=0.7, strokeWidth=1.25, filled=True).encode(
        x=alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
        y=alt.Y('P (yr):Q', title='Orbital Period (yrs)'),
        yOffset=alt.YOffset('jitter:Q'),
        color=alt.condition(
            brush, 'e:Q', alt.value('lightgray'),
            scale=alt.Scale(scheme='viridis'), title='Eccentricity'
        ),
        tooltip=[
            alt.Tooltip('full_name:N', title='Comet:'),
            alt.Tooltip('Epoch:T', title='Date Discovered:'),
            alt.Tooltip('P (yr):Q', title='Period (yr):'),
            alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU):'),
            alt.Tooltip('e:Q', title='Eccentricity:'),
            alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU):')
        ],
    ).properties(title="What characteristics of Near Earth Comets affect its orbital period?",
                width=600, height=400)
)

# Upper plot: x-domain controlled by brush
upper = points.encode(
    x=alt.X('q (AU):Q', title='Perihelion Distance (AU)',
            scale=alt.Scale(domain=brush))
)

# Lower plot: hosts the x brush (encode X here, not Y)
lower = (
    base.mark_point(opacity=0)  # or .mark_tick()
        .properties(height=60)
        .add_params(brush)
        .encode(
            x=alt.X('q (AU):Q', title=None)
        )
)

alt.vconcat(upper, lower)

alt.VConcatChart(...)

In [12]:

brush = alt.selection_interval(encodings=['x'], empty='all')  # when empty -> use all data

decade_param = alt.param(
    name='DecadeParam',
    bind=alt.binding_select(
        options=['All'] + sorted(df["Decade"].unique()),
        name="Decade:"
    ),
    value='All'  # default
)

# Base chart with decade filter (+ optional jitter to reduce overlap)
base = (
    alt.Chart(df)
      .add_params(decade_param, brush)
      .transform_filter(
          (decade_param == 'All') | (alt.datum.Decade == decade_param)
      )
      .transform_calculate(
          jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
      )
)

# --- Left: scatter with brush ---
scatter = (
    base.mark_point(opacity=0.7, filled=True, stroke='white', strokeWidth=0.3)
    .encode(
        x=alt.X('q (AU):Q', title='Perihelion Distance (AU)'),
        y=alt.Y('P (yr):Q', title='Orbital Period (yrs)'),
        yOffset=alt.YOffset('jitter:Q'),
        color=alt.condition(
            brush, 'e:Q', alt.value('lightgray'),
            scale=alt.Scale(scheme='viridis'), title='Eccentricity'
        ),
        tooltip=[
            alt.Tooltip('full_name:N', title='Comet'),
            alt.Tooltip('Epoch:T', title='Date Discovered'),
            alt.Tooltip('P (yr):Q', title='Period (yrs)'),
            alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU)'),
            alt.Tooltip('e:Q', title='Eccentricity'),
            alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU)')
        ],
    )
    .properties(
        title="What characteristics of Near Earth Comets affect orbital period?",
        width=500, height=350
    )
)

# --- Right: Top-10 bar chart (closest MOID) synced to brush ---
bars = (
    base
      # use the brush; when empty='all', this shows top-10 from the full (filtered-by-decade) set
      .transform_filter(brush)
      # remove null MOID to avoid ranking issues
      .transform_filter("isValid(datum['MOID (AU)'])")
      # rank by smallest MOID
      .transform_window(
          rank='rank()',
          sort=[alt.SortField('MOID (AU)', order='ascending')]
      )
      .transform_filter(alt.datum.rank <= 10)
      .encode(
          y=alt.Y('full_name:N',
                  title='Top 10 (closest MOID)',
                  sort='-x'),                           # sort bars by value
          x=alt.X('MOID (AU):Q', title='Earth Distance (AU)'),
          color=alt.Color('e:Q', title='Eccentricity',
                          scale=alt.Scale(scheme='viridis'))
      )
      .mark_bar()
      .properties(width=250, height=350, title='Top 10 in current view/selection')
)

alt.hconcat(scatter, bars)

alt.HConcatChart(...)

In [13]:
heat = (
    alt.Chart(df).transform_calculate(
          moid_num="toNumber(datum['MOID (AU)'])",
          p_num="toNumber(datum['P (yr)'])"
      ).transform_filter(
          "isValid(datum.moid_num) && datum.moid_num > 0"
      ).transform_filter(
          "isValid(datum.p_num) && datum.p_num > 0"
      ).transform_calculate(
          log_moid="log(datum.moid_num)/log(10)",
          log_p="log(datum.p_num)/log(10)"
      ).mark_rect().encode(
          x=alt.X('log_moid:Q', bin=alt.Bin(maxbins=30),
                  title='log10(MOID, AU)'),
          y=alt.Y('log_p:Q',    bin=alt.Bin(maxbins=30),
                  title='log10(Period, years)'),
          color=alt.Color('count():Q', title='Comets')
      ).properties(
          width=900, height=420, 
          title='How close and how often does each comet get to Earth?'
      )
)
heat

alt.Chart(...)

In [14]:
# useless

In [15]:
# --- Selections/controls ---
brush = alt.selection_interval(encodings=['x'], empty='all')

decade_param = alt.param(
    name='DecadeParam',
    bind=alt.binding_select(options=['All'] + sorted(df["Decade"].unique()), name="Decade: "),
    value='All'
)

# X-axis toggle: choose between Perihelion (q) and MOID
xmode = alt.param(
    name='XMode',
    bind=alt.binding_select(options=['Perihelion (q)', 'MOID'], name='X-axis: '),
    value='Perihelion (q)'
)

# --- Base chart (shared filters + jitter + x_val compute) ---
base = (
    alt.Chart(df)
      .add_params(decade_param, xmode, brush)
      .transform_filter((decade_param == 'All') | (alt.datum.Decade == decade_param))
      .transform_calculate(
          jitter='sqrt(-2*log(random()))*cos(2*PI*random())',
          # switch x value based on XMode; coerce to number to avoid type issues
          x_val="XMode == 'MOID' ? toNumber(datum['MOID (AU)']) : toNumber(datum['q (AU)'])",
          x_label="XMode == 'MOID' ? 'MOID (AU)' : 'Perihelion Distance (AU)'"  # for tooltips
      )
)

# --- Left: scatter with brush (x toggles between q and MOID) ---
scatter = (
    base.mark_point(opacity=0.7, filled=True, stroke='white', strokeWidth=0.3)
        .encode(
            x=alt.X('x_val:Q', title='Distance (AU)'),   # one channel that switches via x_val
            y=alt.Y('P (yr):Q', title='Orbital Period (yrs)'),
            yOffset=alt.YOffset('jitter:Q'),
            color=alt.condition(
                brush, 'e:Q', alt.value('lightgray'),
                scale=alt.Scale(scheme='viridis'), title='Eccentricity'
            ),
            tooltip=[
                alt.Tooltip('full_name:N', title='Comet'),
                alt.Tooltip('Epoch:T', title='Date Discovered'),
                alt.Tooltip('P (yr):Q', title='Period (yrs)'),
                alt.Tooltip('q (AU):Q', title='Perihelion Distance (AU)'),
                alt.Tooltip('MOID (AU):Q', title='Earth Distance (MOID, AU)'),
                alt.Tooltip('e:Q', title='Eccentricity'),
                alt.Tooltip('x_label:N', title='X-axis')
            ],
        )
        .properties(
            title="Perihelion/MOID vs Orbital Period (use X-axis selector)",
            width=500, height=350
        )
)

# --- Right: Top-10 bar chart (closest MOID) synced to current brush ---
bars = (
    base
      .transform_filter("isValid(datum['MOID (AU)'])")
      .transform_filter(brush)  # respects the current x brush, whether q or MOID
      .transform_window(
          rank='rank()',
          sort=[alt.SortField('MOID (AU)', order='ascending')]
      )
      .transform_filter(alt.datum.rank <= 10)
      .encode(
          y=alt.Y('full_name:N', title='Top 10 (closest MOID)', sort='x'),
          x=alt.X('MOID (AU):Q', title='Earth Distance (MOID, AU)'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Comet'),
              alt.Tooltip('MOID (AU):Q', title='Earth Distance (AU)'),
              alt.Tooltip('P (yr):Q', title='Period (yrs)')
          ]
      )
      .mark_bar()
      .properties(width=250, height=350, title='Top 10 in current view/selection')
)

alt.hconcat(scatter, bars)

alt.HConcatChart(...)

In [16]:
# ---------------- Controls ----------------
brush = alt.selection_interval(encodings=['x'], empty='all')

decade_param = alt.param(
    name='DecadeParam',
    bind=alt.binding_select(options=['All'] + sorted(df["Decade"].unique()), name="Decade: "),
    value='All'
)

Q1 = "What characteristics impact a comet’s orbital period and distance from Earth?"
Q2 = "How close and how often does each comet get to Earth?"

view_param = alt.param(
    name='ViewParam',
    bind=alt.binding_select(options=[Q1, Q2], name='View: '),
    value=Q1
)

# ---------------- Base (shared) ----------------
base = (
    alt.Chart(df)
      .add_params(decade_param, view_param, brush)
      .transform_filter((decade_param == 'All') | (alt.datum.Decade == decade_param))
      .transform_calculate(
          jitter='sqrt(-2*log(random()))*cos(2*PI*random())',
          p_num="toNumber(datum['P (yr)'])",
          q_num="toNumber(datum['q (AU)'])",
          moid_num="toNumber(datum['MOID (AU)'])"
      )
      .transform_filter("isFinite(datum.p_num)")
)

# One scatter that switches X **field** by view, but keeps a single, simple axis label.
# (This avoids duplicate axes / clutter while keeping the spread you liked.)
scatter = (
    base
      .transform_calculate(
          x_val=f"(ViewParam == '{Q2}') ? datum.moid_num : datum.q_num"
      )
      .transform_filter("isFinite(datum.x_val)")
      .mark_point(opacity=0.75, filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('x_val:Q', title='Distance (AU)'),   # one clean label for both views
          y=alt.Y('p_num:Q', title='Orbital Period (yrs)'),
          yOffset=alt.YOffset('jitter:Q'),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Comet'),
              alt.Tooltip('Epoch:T',     title='Date Discovered'),
              alt.Tooltip('p_num:Q',     title='Period (yrs)'),
              alt.Tooltip('q_num:Q',     title='Perihelion Distance (AU)'),
              alt.Tooltip('moid_num:Q',  title='MOID (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade')
          ],
      )
      .properties(
          title="What characteristics impact a comet’s orbital period and distance from Earth?",
          width=600, height=400
      )
      .add_params(brush)
)

# ---------------- Quadrants (only when MOID view is active) ----------------
# Compute extents on MOID (linear) and Period, then split in half.
quad_stats = (
    alt.Chart(df)
      .add_params(decade_param, view_param)
      .transform_filter((decade_param == 'All') | (alt.datum.Decade == decade_param))
      .transform_filter(f"ViewParam == '{Q2}'")
      .transform_calculate(
          p_num="toNumber(datum['P (yr)'])",
          moid_num="toNumber(datum['MOID (AU)'])"
      )
      .transform_filter("isFinite(datum.p_num) && isFinite(datum.moid_num)")
      .transform_aggregate(aggregate=[
          {'op':'min','field':'moid_num','as':'x_min'},
          {'op':'max','field':'moid_num','as':'x_max'},
          {'op':'min','field':'p_num',   'as':'y_min'},
          {'op':'max','field':'p_num',   'as':'y_max'}
      ])
      .transform_calculate(
          x_mid='(datum.x_min + datum.x_max) / 2',
          y_mid='(datum.y_min + datum.y_max) / 2',
          x_left='(datum.x_min + datum.x_mid) / 2',
          x_right='(datum.x_mid + datum.x_max) / 2',
          y_low='(datum.y_min + datum.y_mid) / 2',
          y_high='(datum.y_mid + datum.y_max) / 2'
      )
)

# Background shading only (no axes here → the scatter owns axes & grid)
vband = quad_stats.mark_rect(color='#1f77b4', opacity=0.08).encode(
    x='x_min:Q', x2='x_mid:Q', y='y_min:Q', y2='y_max:Q'
)
hband = quad_stats.mark_rect(color='#2ca02c', opacity=0.08).encode(
    x='x_min:Q', x2='x_max:Q', y='y_min:Q', y2='y_mid:Q'
)

# Labels on TOP of points (layered after scatter)
label_LL = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_left:Q',  y='y_low:Q',  text=alt.value('Frequent & closer')
)
label_LR = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_right:Q', y='y_low:Q',  text=alt.value('Frequent but distant')
)
label_UL = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_left:Q',  y='y_high:Q', text=alt.value('Rare but closer')
)
label_UR = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_right:Q', y='y_high:Q', text=alt.value('Rare & distant')
)

# Only render the bands/labels when MOID view is selected.
# (When View=Q1, these layers contain no data → nothing draws.)
quads_bg = vband + hband
quad_labels = label_LL + label_LR + label_UL + label_UR

# Make sure axes/grid come from the scatter: scatter first, then background, then labels
main_left = alt.layer(scatter, quads_bg, quad_labels).resolve_scale(x='shared', y='shared')

# ---------------- Bars (Top-10 by smallest MOID; respects brush) ----------------
bars = (
    base
      .transform_filter("isValid(datum['MOID (AU)'])")
      .transform_filter(brush)
      .transform_window(rank='rank()', sort=[alt.SortField('MOID (AU)', order='ascending')])
      .transform_filter(alt.datum.rank <= 10)
      .encode(
          y=alt.Y('full_name:N', title='Top 10 (closest MOID)', sort='x'),
          x=alt.X('MOID (AU):Q', title='Earth Distance (MOID, AU)'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Comet'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)')
          ]
      )
      .mark_bar()
      .properties(width=320, height=400, title='Top 10 in current view/selection')
)

alt.hconcat(main_left, bars)


alt.HConcatChart(...)

In [17]:
# ---------------- Controls ----------------
brush = alt.selection_interval(encodings=['x'], empty='all')

decade_param = alt.param(
    name='DecadeParam',
    bind=alt.binding_select(options=['All'] + sorted(df["Decade"].unique()), name="Decade: "),
    value='All'
)

Q1 = "What characteristics impact a comet’s orbital period and distance from Earth?"
Q2 = "How close and how often does each comet get to Earth?"

view_param = alt.param(
    name='ViewParam',
    bind=alt.binding_select(options=[Q1, Q2], name='View: '),
    value=Q1
)

# ---------------- Base (shared) ----------------
base = (
    alt.Chart(df)
      .add_params(decade_param, view_param, brush)
      .transform_filter((decade_param == 'All') | (alt.datum.Decade == decade_param))
      .transform_calculate(
          jitter='sqrt(-2*log(random()))*cos(2*PI*random())',
          p_num="toNumber(datum['P (yr)'])",
          q_num="toNumber(datum['q (AU)'])",
          moid_num="toNumber(datum['MOID (AU)'])"
      )
      .transform_filter("isFinite(datum.p_num)")
)

# One scatter that switches X **field** by view, but keeps a single, simple axis label.
# (This avoids duplicate axes / clutter while keeping the spread you liked.)
scatter = (
    base
      .transform_calculate(
          x_val=f"(ViewParam == '{Q2}') ? datum.moid_num : datum.q_num"
      )
      .transform_filter("isFinite(datum.x_val)")
      .mark_point(opacity=0.75, filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('x_val:Q', title='Distance (AU)'),   # one clean label for both views
          y=alt.Y('p_num:Q', title='Orbital Period (yrs)'),
          yOffset=alt.YOffset('jitter:Q'),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Comet'),
              alt.Tooltip('Epoch:T',     title='Date Discovered'),
              alt.Tooltip('p_num:Q',     title='Period (yrs)'),
              alt.Tooltip('q_num:Q',     title='Perihelion Distance (AU)'),
              alt.Tooltip('moid_num:Q',  title='MOID (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade')
          ],
      )
      .properties(
          title="What characteristics impact a comet’s orbital period and distance from Earth?",
          width=600, height=400
      )
      .add_params(brush)
)

# ---------------- Quadrants (only when MOID view is active) ----------------
# Compute extents on MOID (linear) and Period, then split in half.
quad_stats = (
    alt.Chart(df)
      .add_params(decade_param, view_param)
      .transform_filter((decade_param == 'All') | (alt.datum.Decade == decade_param))
      .transform_filter(f"ViewParam == '{Q2}'")
      .transform_calculate(
          p_num="toNumber(datum['P (yr)'])",
          moid_num="toNumber(datum['MOID (AU)'])"
      )
      .transform_filter("isFinite(datum.p_num) && isFinite(datum.moid_num)")
      .transform_aggregate(aggregate=[
          {'op':'min','field':'moid_num','as':'x_min'},
          {'op':'max','field':'moid_num','as':'x_max'},
          {'op':'min','field':'p_num',   'as':'y_min'},
          {'op':'max','field':'p_num',   'as':'y_max'}
      ])
      .transform_calculate(
          x_mid='(datum.x_min + datum.x_max) / 2',
          y_mid='(datum.y_min + datum.y_max) / 2',
          x_left='(datum.x_min + datum.x_mid) / 2',
          x_right='(datum.x_mid + datum.x_max) / 2',
          y_low='(datum.y_min + datum.y_mid) / 2',
          y_high='(datum.y_mid + datum.y_max) / 2'
      )
)

# Background shading only (no axes here → the scatter owns axes & grid)
vband = quad_stats.mark_rect(color='#1f77b4', opacity=0.08).encode(
    x='x_min:Q', x2='x_mid:Q', y='y_min:Q', y2='y_max:Q'
)
hband = quad_stats.mark_rect(color='#2ca02c', opacity=0.08).encode(
    x='x_min:Q', x2='x_max:Q', y='y_min:Q', y2='y_mid:Q'
)

# Labels on TOP of points (layered after scatter)
label_LL = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_left:Q',  y='y_low:Q',  text=alt.value('Frequent & closer')
)
label_LR = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_right:Q', y='y_low:Q',  text=alt.value('Frequent but distant')
)
label_UL = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_left:Q',  y='y_high:Q', text=alt.value('Rare but closer')
)
label_UR = quad_stats.mark_text(fontSize=12, fontWeight='bold').encode(
    x='x_right:Q', y='y_high:Q', text=alt.value('Rare & distant')
)

# Only render the bands/labels when MOID view is selected.
# (When View=Q1, these layers contain no data → nothing draws.)
quads_bg = vband + hband
quad_labels = label_LL + label_LR + label_UL + label_UR

# Make sure axes/grid come from the scatter: scatter first, then background, then labels
main_left = alt.layer(scatter, quads_bg, quad_labels).resolve_scale(x='shared', y='shared')

# ---------------- Bars (Top-10 by smallest MOID; respects brush) ----------------
bars = (
    base
      .transform_filter("isValid(datum['MOID (AU)'])")
      .transform_filter(brush)
      .transform_window(rank='rank()', sort=[alt.SortField('MOID (AU)', order='ascending')])
      .transform_filter(alt.datum.rank <= 10)
      .encode(
          y=alt.Y('full_name:N', title='Top 10 (closest MOID)', sort='x'),
          x=alt.X('MOID (AU):Q', title='Earth Distance (MOID, AU)'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Comet'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)')
          ]
      )
      .mark_bar()
      .properties(width=320, height=400, title='Top 10 in current view/selection')
)

alt.hconcat(main_left, bars)

alt.HConcatChart(...)

In [18]:
# Selection interval (brush)
brush = alt.selection_interval()

# Dropdown filter for Decade
decade_select = alt.param(
    bind=alt.binding_select(options=['All'] + sorted(df['Decade'].unique()), name='Decade:'),
    value='All'
)

# ---------- LEFT: Perihelion vs Orbital Period
left = (
    alt.Chart(df)
      .add_params(decade_select, brush)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('q (AU):Q', axis=alt.Axis(title='Perihelion Distance (AU)', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(brush, 'e:Q', alt.value('lightgray'),
                               scale=alt.Scale(scheme='viridis'), title='Eccentricity'),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('Epoch:T', title='Discovered'),
              alt.Tooltip('P (yr):Q', title='Period (yrs)'),
              alt.Tooltip('q (AU):Q', title='Perihelion (AU)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('e:Q', title='Eccentricity'),
              alt.Tooltip('Decade:N', title='Decade'),
          ]
      )
      .properties(width=350, height=300, title='Perihelion vs Orbital Period')
)

# ---------- RIGHT: MOID vs Orbital Period
right = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('MOID (AU):Q', axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(brush, 'e:Q', alt.value('lightgray'),
                               scale=alt.Scale(scheme='viridis'), title='Eccentricity'),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('P (yr):Q', title='Period (yrs)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('q (AU):Q', title='Perihelion (AU)'),
              alt.Tooltip('e:Q', title='Eccentricity'),
              alt.Tooltip('Decade:N', title='Decade'),
          ]
      )
      .properties(width=350, height=300, title='MOID vs Orbital Period')
)

# Side-by-side layout
chart = (left | right).resolve_scale(color='shared')

chart


alt.HConcatChart(...)

In [19]:
# Selection interval (brush)
brush = alt.selection_interval()

# Dropdown filter for Decade
decade_select = alt.param(
    bind=alt.binding_select(options=['All'] + sorted(df['Decade'].unique()), name='Decade:'),
    value='All'
)

# ---------- LEFT: Kepler (Semi-major axis a) vs Orbital Period
left = (
    alt.Chart(df)
      .add_params(decade_select, brush)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('Semi-major Axis:Q', axis=alt.Axis(title='Semi-major Axis (AU)', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(brush, 'e:Q', alt.value('lightgray'),
                               scale=alt.Scale(scheme='viridis'), title='Eccentricity'),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('Epoch:T',     title='Discovered'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('a (AU):Q',    title='Semi-major Axis (AU)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=350, height=300, title="Semi-major Axis vs Orbital Period (Kepler's 3rd Law)")
)

# ---------- RIGHT: MOID vs Orbital Period (unchanged)
right = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('MOID (AU):Q', axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(brush, 'e:Q', alt.value('lightgray'),
                               scale=alt.Scale(scheme='viridis'), title='Eccentricity'),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('a (AU):Q',    title='Semi-major Axis (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=350, height=300, title='MOID vs Orbital Period')
)

# Side-by-side layout
chart = (left | right).resolve_scale(color='shared')

chart


alt.HConcatChart(...)

In [20]:
brush = alt.selection_interval(empty='all')

decade_select = alt.param(
    bind=alt.binding_select(options=['All'] + sorted(df['Decade'].unique()), name='Decade:'),
    value='All'
)

# -----------------------------
# LEFT: Perihelion vs Period
# -----------------------------
left = (
    alt.Chart(df)
      .add_params(decade_select, brush)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('q (AU):Q', axis=alt.Axis(title='Perihelion Distance (AU)', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('Epoch:T', title='Discovered'),
              alt.Tooltip('P (yr):Q', title='Period (yrs)'),
              alt.Tooltip('q (AU):Q', title='Perihelion (AU)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('e:Q', title='Eccentricity'),
              alt.Tooltip('Decade:N', title='Decade'),
          ]
      )
      .properties(width=350, height=300, title='Perihelion vs Orbital Period')
)

# -----------------------------
# RIGHT: MOID vs Period
# -----------------------------
right = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('MOID (AU):Q', axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('P (yr):Q', title='Period (yrs)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('q (AU):Q', title='Perihelion (AU)'),
              alt.Tooltip('e:Q', title='Eccentricity'),
              alt.Tooltip('Decade:N', title='Decade'),
          ]
      )
      .properties(width=350, height=300, title='MOID vs Orbital Period')
)

# Top row: side-by-side scatterplots (unchanged)
top_row = (left | right).resolve_scale(color='shared')

# ----------------------------------------------------
# PRIORITY LIST METRIC + TOP-10 BAR CHART (below)
# Priority = average of normalized proximity (1/MOID) and frequency (1/Period)
# ----------------------------------------------------
bars = (
    alt.Chart(df)
      .add_params(decade_select)
      # 1) Apply the same decade filter
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      # 2) Restrict to current brush selection from the LEFT chart (when empty='all', this is the full set)
      .transform_filter(brush)
      # 3) Numeric casts + safe inverses
      .transform_calculate(
          p_num   ="toNumber(datum['P (yr)'])",
          moid_num="toNumber(datum['MOID (AU)'])",
          inv_p   ="(isFinite(toNumber(datum['P (yr)'])) && toNumber(datum['P (yr)'])>0) ? 1/toNumber(datum['P (yr)']) : 0",
          inv_moid="(isFinite(toNumber(datum['MOID (AU)'])) && toNumber(datum['MOID (AU)'])>0) ? 1/toNumber(datum['MOID (AU)']) : 0"
      )
      # 4) Get min/max for normalization over the currently filtered set
      .transform_joinaggregate(
          invp_min='min(inv_p)',    invp_max='max(inv_p)',
          invm_min='min(inv_moid)', invm_max='max(inv_moid)'
      )
      # 5) Normalize and compute priority score
      .transform_calculate(
          freq_norm="(datum.invp_max>datum.invp_min) ? (datum.inv_p - datum.invp_min)/(datum.invp_max - datum.invp_min) : 0",
          prox_norm="(datum.invm_max>datum.invm_min) ? (datum.inv_moid - datum.invm_min)/(datum.invm_max - datum.invm_min) : 0",
          priority="0.5 * (datum.freq_norm + datum.prox_norm)"
      )
      # 6) Rank and keep top 10 (highest priority first)
      .transform_window(
          rank='rank()', sort=[alt.SortField('priority', order='descending')]
      )
      .transform_filter(alt.datum.rank <= 10)
      # 7) Bar chart
      .mark_bar()
      .encode(
          y=alt.Y('full_name:N', sort='-x', title='Top 10 Priority (current view/selection)'),
          x=alt.X('priority:Q', title='Priority Score'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('priority:Q',  title='Priority Score', format='.3f'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
          ]
      )
      .properties(width=720, height=280, title='Watchlist: Top 10 by Priority (closer & more frequent)')
)

# Final layout: top charts + priority bars
final = alt.vconcat(top_row, bars, spacing=24)

final

alt.VConcatChart(...)

In [30]:
# ----- Sizes -----
SCATTER_W, SCATTER_H = 400, 280   # bigger scatters
BARS_W,    BARS_H    = 640, 160   # smaller watchlist


# -----------------------------
# Helper: caption block (no overlap)
# ----------------------------
def caption_block(lines, width=320, line_height=14, top_pad=4):
    df_cap = pd.DataFrame({"line": list(range(1, len(lines)+1)), "text": lines})
    return (
        alt.Chart(df_cap)
          .mark_text(align="left", baseline="top", fontSize=12, dx=0, dy=0, color="#444")
          .encode(
              x=alt.value(0),                      # left-align inside the caption area
              y=alt.Y('line:O', axis=None),        # each row gets its own y
              text='text:N'
          )
          .properties(
              width=width,
              height=top_pad + len(lines)*line_height
          )
    )

# -----------------------------
# Controls (unchanged)
# -----------------------------
brush = alt.selection_interval(empty='all')

decade_select = alt.param(
    bind=alt.binding_select(options=['All'] + sorted(df['Decade'].unique()), name='Decade:'),
    value='All'
)
# ----- Quadrant setup for MOID chart (even split across domain) -----
p_vals   = pd.to_numeric(df['P (yr)'], errors='coerce')
moid_vals= pd.to_numeric(df['MOID (AU)'], errors='coerce')

p_min,   p_max   = float(p_vals.min()),    float(p_vals.max())
moid_min, moid_max = float(moid_vals.min()), float(moid_vals.max())

# Even split at midpoints of the domains (not medians)
p_mid   = 0.5 * (p_min + p_max)
moid_mid= 0.5 * (moid_min + moid_max)

quads_df = pd.DataFrame({
    'x':   [moid_min,  moid_mid,  moid_min,  moid_mid ],
    'x2':  [moid_mid,  moid_max,  moid_mid,  moid_max ],
    'y':   [p_mid,     p_mid,     p_min,     p_min    ],
    'y2':  [p_max,     p_max,     p_mid,     p_mid    ],
    'label': [
        'Rare but closer',      # top-left
        'Rare & distant',       # top-right
        'Frequent & closer',    # bottom-left
        'Frequent but distant'  # bottom-right
    ],
    # gentle, even tints (alternating) – color is carried by dots, not the panes
    'fill': ['#dfe8f6', '#efe9fa', '#e8f4ee', '#f1f7ea']
})
quads_df['cx'] = 0.5*(quads_df['x']  + quads_df['x2'])
quads_df['cy'] = 0.5*(quads_df['y']  + quads_df['y2'])



# -----------------------------
# LEFT: Perihelion vs Period (smaller size)
# -----------------------------
left = (
    alt.Chart(df)
      .add_params(decade_select, brush)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('q (AU):Q', axis=alt.Axis(title='Perihelion Distance (AU)', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)',   grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('Epoch:T',     title='Discovered'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('q (AU):Q',    title='Perihelion (AU)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=SCATTER_W, height=SCATTER_H, title='Perihelion vs Orbital Period')
)

left_caption = caption_block(
    [
        "What this shows: Return frequency (y) vs perihelion distance (x).",
        "Why it matters: Shorter periods + smaller perihelion → more time near the Sun.",
        "Tip: Drag a rectangle to highlight — selection links to the MOID chart."
    ],
    width=SCATTER_W
)

left_block = alt.vconcat(left, left_caption, spacing=6)


# -----------------------------
# RIGHT: MOID vs Period (with quadrants)
# -----------------------------
quad_rects = (
    alt.Chart(quads_df)
      .mark_rect(opacity=0.18)   # a touch stronger to be visible, still subtle
      .encode(
          x=alt.X('x:Q',  scale=alt.Scale(domain=[moid_min, moid_max]),
                 axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          x2='x2:Q',
          y=alt.Y('y:Q',  scale=alt.Scale(domain=[p_min, p_max]),
                 axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          y2='y2:Q',
          color=alt.Color('fill:N', legend=None, scale=None)
      )
      .properties(width=SCATTER_W, height=SCATTER_H)
)

quad_labels = (
    alt.Chart(quads_df)
      .mark_text(fontWeight='bold', color='#2b2b2b')
      .encode(
          x=alt.X('cx:Q', scale=alt.Scale(domain=[moid_min, moid_max])),
          y=alt.Y('cy:Q', scale=alt.Scale(domain=[p_min,    p_max])),
          text='label:N'
      )
)

right_points = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('MOID (AU):Q', scale=alt.Scale(domain=[moid_min, moid_max]),
                 axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          y=alt.Y('P (yr):Q',     scale=alt.Scale(domain=[p_min, p_max]),
                 axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('q (AU):Q',    title='Perihelion (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=SCATTER_W, height=SCATTER_H, title='MOID vs Orbital Period')
)

right = alt.layer(quad_rects, right_points, quad_labels)

right_caption = caption_block(
    [
        "What this shows: MOID vs return frequency (period).",
        "Why it matters: Smaller MOID → closer Earth-orbit intersections; short period → more often.",
        "Interpretation: Low MOID + short period → higher monitoring interest."
    ],
    width=SCATTER_W
)

right_block = alt.vconcat(right, right_caption, spacing=6)

# -----------------------------
# TOP ROW: side-by-side with shared color
# -----------------------------
top_row = (left_block | right_block).resolve_scale(color='shared').properties(spacing=14)

# ----------------------------------------------------
# PRIORITY WATCHLIST (same logic; smaller + caption block)
# ----------------------------------------------------
bars = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .transform_filter(brush)
      .transform_calculate(
          p_num   ="toNumber(datum['P (yr)'])",
          moid_num="toNumber(datum['MOID (AU)'])",
          inv_p   ="(isFinite(toNumber(datum['P (yr)'])) && toNumber(datum['P (yr)'])>0) ? 1/toNumber(datum['P (yr)']) : 0",
          inv_moid="(isFinite(toNumber(datum['MOID (AU)'])) && toNumber(datum['MOID (AU)'])>0) ? 1/toNumber(datum['MOID (AU)']) : 0"
      )
      .transform_joinaggregate(
          invp_min='min(inv_p)',    invp_max='max(inv_p)',
          invm_min='min(inv_moid)', invm_max='max(inv_moid)'
      )
      .transform_calculate(
          freq_norm="(datum.invp_max>datum.invp_min) ? (datum.inv_p - datum.invp_min)/(datum.invp_max - datum.invp_min) : 0",
          prox_norm="(datum.invm_max>datum.invm_min) ? (datum.inv_moid - datum.invm_min)/(datum.invm_max - datum.invm_min) : 0",
          priority="0.5 * (datum.freq_norm + datum.prox_norm)"
      )
      .transform_window(rank='rank()', sort=[alt.SortField('priority', order='descending')])
      .transform_filter(alt.datum.rank <= 10)
      .mark_bar()
      .encode(
          y=alt.Y('full_name:N', sort='-x', title='Top 10 Priority (current view/selection)'),
          x=alt.X('priority:Q', title='Priority Score'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('priority:Q',  title='Priority Score', format='.3f'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
          ]
      )
      .properties(width=BARS_W, height=BARS_H, title='Watchlist: Top 10 by Priority (closer & more frequent)')
)

bars_caption = caption_block(
    [
        "What this shows: Screening metric combining proximity (1/MOID) and frequency (1/Period).",
        "Why it matters: Creates an actionable shortlist for monitoring.",
        "Note: Not a risk probability—size, inclination, uncertainties matter."
    ],
    width=BARS_W
)

bars_block = alt.vconcat(bars, bars_caption, spacing=6)

#Final
top_row = (left_block | right_block).resolve_scale(color='shared').properties(spacing=16)

final = alt.vconcat(
    top_row,
    bars_block,
    spacing=18
).configure_axis(
    labelFontSize=10, titleFontSize=12
).configure_legend(
    labelFontSize=10, titleFontSize=12
)

final

alt.VConcatChart(...)

In [34]:
import altair as alt
import pandas as pd

# -----------------------------
# Sizes & layout
# -----------------------------
SCATTER_W, SCATTER_H = 420, 290          # slightly bigger scatters
TOP_SPACING           = 16
TOTAL_TOP_W           = SCATTER_W*2 + TOP_SPACING

BARS_W   = int(TOTAL_TOP_W * 0.62)        # narrower bars
BARS_H   = 170
CAPTION_LINE_H        = 14

# -----------------------------
# Small caption helper (no overlap)
# -----------------------------
def caption_block(lines, width=320, line_height=14, top_pad=4, fontsize=12):
    df_cap = pd.DataFrame({"line": list(range(1, len(lines)+1)), "text": lines})
    return (
        alt.Chart(df_cap)
          .mark_text(align="left", baseline="top", fontSize=fontsize, dx=0, dy=0, color="#444")
          .encode(x=alt.value(0), y=alt.Y('line:O', axis=None), text='text:N')
          .properties(width=width, height=top_pad + len(lines)*line_height)
    )

# -----------------------------
# Controls
# -----------------------------
brush = alt.selection_interval(empty='all')
decade_select = alt.param(
    bind=alt.binding_select(options=['All'] + sorted(df['Decade'].unique()), name='Decade:'),
    value='All'
)

# -----------------------------
# Domains & quadrant midpoints
# -----------------------------
p_vals    = pd.to_numeric(df['P (yr)'],      errors='coerce')
moid_vals = pd.to_numeric(df['MOID (AU)'],   errors='coerce')

p_min, p_max         = float(p_vals.min()),      float(p_vals.max())
moid_min, moid_max   = float(moid_vals.min()),   float(moid_vals.max())
p_mid,  moid_mid     = 0.5*(p_min+p_max),        0.5*(moid_min+moid_max)

quads_df = pd.DataFrame({
    'x':   [moid_min,  moid_mid,  moid_min,  moid_mid ],
    'x2':  [moid_mid,  moid_max,  moid_mid,  moid_max ],
    'y':   [p_mid,     p_mid,     p_min,     p_min    ],
    'y2':  [p_max,     p_max,     p_mid,     p_mid    ],
    'label': [
        'Rare but closer',
        'Rare & distant',
        'Frequent & closer',
        'Frequent but distant'
    ],
    # gentle, even tints; will use as constant fills
    'fill': ['#dfe8f6', '#efe9fa', '#e8f4ee', '#f1f7ea']
})
quads_df['cx'] = 0.5*(quads_df['x'] + quads_df['x2'])
quads_df['cy'] = 0.5*(quads_df['y'] + quads_df['y2'])

# -----------------------------
# LEFT: Perihelion vs Period
# -----------------------------
left = (
    alt.Chart(df)
      .add_params(decade_select, brush)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('q (AU):Q', axis=alt.Axis(title='Perihelion Distance (AU)', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)',   grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('Epoch:T',     title='Discovered'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('q (AU):Q',    title='Perihelion (AU)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=SCATTER_W, height=SCATTER_H, title='Perihelion vs Orbital Period')
)

left_caption_lines = [
    "What this shows: Return frequency (y) vs perihelion distance (x).",
    "Why it matters: Shorter periods + smaller perihelion → more time near the Sun.",
    "Tip: Drag a rectangle to highlight — selection links to the MOID chart."
]
left_caption = caption_block(left_caption_lines, width=SCATTER_W, line_height=CAPTION_LINE_H)
left_block = alt.vconcat(left, left_caption, spacing=6)

# -----------------------------
# RIGHT: MOID vs Period (with quadrant shading)
# -----------------------------
quad_rects = (
    alt.Chart(quads_df)
      .mark_rect(stroke=None, fillOpacity=0.22)   # fillOpacity ensures visible tints
      .encode(
          x=alt.X('x:Q',  scale=alt.Scale(domain=[moid_min, moid_max])),
          x2='x2:Q',
          y=alt.Y('y:Q',  scale=alt.Scale(domain=[p_min, p_max])),
          y2='y2:Q',
          color=alt.value('#ffffff')               # base; we'll set fill via condition below
      )
      .properties(width=SCATTER_W, height=SCATTER_H)
)

# Because constant fills per row are easiest via transform & mark, we layer 4 colored rects:
quad_layers = []
for i in range(4):
    layer = (
        alt.Chart(quads_df.iloc[[i]])
          .mark_rect(stroke=None, fill=quads_df.loc[i, 'fill'], fillOpacity=0.22)
          .encode(
              x=alt.X('x:Q',  scale=alt.Scale(domain=[moid_min, moid_max])),
              x2='x2:Q',
              y=alt.Y('y:Q',  scale=alt.Scale(domain=[p_min, p_max])),
              y2='y2:Q'
          )
          .properties(width=SCATTER_W, height=SCATTER_H)
    )
    quad_layers.append(layer)
quad_rects = alt.layer(*quad_layers)

quad_labels = (
    alt.Chart(quads_df)
      .mark_text(fontWeight='bold', color='#2b2b2b')
      .encode(
          x=alt.X('cx:Q', scale=alt.Scale(domain=[moid_min, moid_max])),
          y=alt.Y('cy:Q', scale=alt.Scale(domain=[p_min,    p_max])),
          text='label:N'
      )
)

right_points = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('MOID (AU):Q',
                  scale=alt.Scale(domain=[moid_min, moid_max]),
                  axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          y=alt.Y('P (yr):Q',
                  scale=alt.Scale(domain=[p_min, p_max]),
                  axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('q (AU):Q',    title='Perihelion (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=SCATTER_W, height=SCATTER_H, title='MOID vs Orbital Period')
)

right = alt.layer(quad_rects, right_points, quad_labels)

right_caption_lines = [
    "What this shows: MOID vs return frequency (period).",
    "Why it matters: Smaller MOID → closer Earth-orbit intersections; short period → more often.",
    "Interpretation: Low MOID + short period → higher monitoring interest."
]
right_caption = caption_block(right_caption_lines, width=SCATTER_W, line_height=CAPTION_LINE_H)
right_block = alt.vconcat(right, right_caption, spacing=6)

# -----------------------------
# TOP ROW
# -----------------------------
top_row = (left_block | right_block).resolve_scale(color='shared').properties(spacing=TOP_SPACING)

# -----------------------------
# Watchlist (labels wrapped; full width = match top row)
# -----------------------------
TOTAL_TOP_W = SCATTER_W*2 + TOP_SPACING
BARS_W      = TOTAL_TOP_W
BARS_H      = 170

bars_caption_lines = [
    "What this shows: Screening metric combining proximity (1/MOID) and frequency (1/Period).",
    "Why it matters: Creates an actionable shortlist for monitoring.",
    "Note: Not a risk probability—size, inclination, uncertainties matter."
]

bars = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .transform_filter(brush)
      .transform_calculate(
          # wrap long names at whitespace after ~18 chars
          label_wrap="replace(datum['full_name'], /(.{18,}?)(\\s)/g, '$1\\n')",
          p_num   ="toNumber(datum['P (yr)'])",
          moid_num="toNumber(datum['MOID (AU)'])",
          inv_p   ="(isFinite(toNumber(datum['P (yr)'])) && toNumber(datum['P (yr)'])>0) ? 1/toNumber(datum['P (yr)']) : 0",
          inv_moid="(isFinite(toNumber(datum['MOID (AU)'])) && toNumber(datum['MOID (AU)'])>0) ? 1/toNumber(datum['MOID (AU)']) : 0"
      )
      .transform_joinaggregate(
          invp_min='min(inv_p)',    invp_max='max(inv_p)',
          invm_min='min(inv_moid)', invm_max='max(inv_moid)'
      )
      .transform_calculate(
          freq_norm="(datum.invp_max>datum.invp_min) ? (datum.inv_p - datum.invp_min)/(datum.invp_max - datum.invp_min) : 0",
          prox_norm="(datum.invm_max>datum.invm_min) ? (datum.inv_moid - datum.invm_min)/(datum.invm_max - datum.invm_min) : 0",
          priority="0.5 * (datum.freq_norm + datum.prox_norm)"
      )
      .transform_window(rank='rank()', sort=[alt.SortField('priority', order='descending')])
      .transform_filter(alt.datum.rank <= 10)
      .mark_bar()
      .encode(
          y=alt.Y('label_wrap:N',
                  sort='-x',
                  title='Top 10 Priority (current view/selection)',
                  axis=alt.Axis(labelLimit=280, labelPadding=4)),
          x=alt.X('priority:Q', title='Priority Score'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('priority:Q',  title='Priority Score', format='.3f'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
          ]
      )
      .properties(width=BARS_W, height=BARS_H, title='Watchlist: Top 10 by Priority (closer & more frequent)')
)

bars_caption = caption_block(bars_caption_lines, width=BARS_W, line_height=CAPTION_LINE_H)
bars_block   = alt.vconcat(bars, bars_caption, spacing=6)

# -----------------------------
# FINAL (no spacer signals → no error)
# -----------------------------
final = alt.vconcat(
    (left_block | right_block).resolve_scale(color='shared').properties(spacing=TOP_SPACING),
    bars_block,
    spacing=18
).configure_axis(
    labelFontSize=10, titleFontSize=12
).configure_legend(
    labelFontSize=10, titleFontSize=12
)

final


alt.VConcatChart(...)

In [45]:

# -----------------------------
# Sizes & layout
# -----------------------------
SCATTER_W, SCATTER_H = 420, 290          # slightly bigger scatters
TOP_SPACING           = 16
TOTAL_TOP_W           = SCATTER_W*2 + TOP_SPACING

# ↓ shorter bars (about ~60% of top row width)
BARS_W   = int(TOTAL_TOP_W * 0.60)
BARS_H   = 170
CAPTION_LINE_H        = 14

# -----------------------------
# Small caption helper (no overlap)
# -----------------------------
def caption_block(lines, width=320, line_height=14, top_pad=4, fontsize=12):
    df_cap = pd.DataFrame({"line": list(range(1, len(lines)+1)), "text": lines})
    return (
        alt.Chart(df_cap)
          .mark_text(align="left", baseline="top", fontSize=fontsize, dx=0, dy=0, color="#444")
          .encode(x=alt.value(0), y=alt.Y('line:O', axis=None), text='text:N')
          .properties(width=width, height=top_pad + len(lines)*line_height)
    )

# -----------------------------
# Controls
# -----------------------------
# Replace your brush definition with:
brush = alt.selection_interval(empty='all')
decade_select = alt.param(
    bind=alt.binding_select(options=['All'] + sorted(df['Decade'].unique()), name='Decade:'),
    value='All'
)

# -----------------------------
# Domains & quadrant midpoints
# -----------------------------
p_vals    = pd.to_numeric(df['P (yr)'],      errors='coerce')
moid_vals = pd.to_numeric(df['MOID (AU)'],   errors='coerce')

p_min, p_max         = float(p_vals.min()),      float(p_vals.max())
moid_min, moid_max   = float(moid_vals.min()),   float(moid_vals.max())
p_mid,  moid_mid     = 0.5*(p_min+p_max),        0.5*(moid_min+moid_max)

# Slightly more distinct but still soft quadrant fills
quads_df = pd.DataFrame({
    'x':   [moid_min,  moid_mid,  moid_min,  moid_mid ],
    'x2':  [moid_mid,  moid_max,  moid_mid,  moid_max ],
    'y':   [p_mid,     p_mid,     p_min,     p_min    ],
    'y2':  [p_max,     p_max,     p_mid,     p_mid    ],
    'label': [
        'Rare but closer',
        'Rare & distant',
        'Frequent & closer',
        'Frequent but distant'
    ],
    # updated tints
    'fill': ['#d8e7ff', '#f0dbff', '#e3f5e1', '#fff1d6']
})
quads_df['cx'] = 0.5*(quads_df['x'] + quads_df['x2'])
quads_df['cy'] = 0.5*(quads_df['y'] + quads_df['y2'])

# -----------------------------
# LEFT: Perihelion vs Period
# -----------------------------
left = (
    alt.Chart(df)
      .add_params(decade_select, brush)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('q (AU):Q', axis=alt.Axis(title='Perihelion Distance (AU)', grid=True)),
          y=alt.Y('P (yr):Q', axis=alt.Axis(title='Orbital Period (yrs)',   grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('Epoch:T',     title='Discovered'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('q (AU):Q',    title='Perihelion (AU)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=SCATTER_W, height=SCATTER_H, title='Perihelion vs Orbital Period')
)

left_caption_lines = [
    "What this shows: Return frequency (y) vs perihelion distance (x).",
    "Why it matters: Shorter periods + smaller perihelion → more time near the Sun.",
    "Tip: Drag a rectangle to highlight — selection links to the MOID chart."
]
left_caption = caption_block(left_caption_lines, width=SCATTER_W, line_height=CAPTION_LINE_H)
left_block  = alt.concat(left,  left_caption,  columns=1, spacing=6)

# -----------------------------
# RIGHT: MOID vs Period (with quadrant shading)
# -----------------------------
# Layer 4 colored rects with slightly higher opacity for clarity
quad_layers = []
for i in range(4):
    layer = (
        alt.Chart(quads_df.iloc[[i]])
          .mark_rect(stroke=None, fill=quads_df.loc[i, 'fill'], fillOpacity=0.30)
          .encode(
              x=alt.X('x:Q',  scale=alt.Scale(domain=[moid_min, moid_max])),
              x2='x2:Q',
              y=alt.Y('y:Q',  scale=alt.Scale(domain=[p_min, p_max])),
              y2='y2:Q'
          )
          .properties(width=SCATTER_W, height=SCATTER_H)
    )
    quad_layers.append(layer)
quad_rects = alt.layer(*quad_layers)

quad_labels = (
    alt.Chart(quads_df)
      .mark_text(fontWeight='bold', color='#2b2b2b')
      .encode(
          x=alt.X('cx:Q', scale=alt.Scale(domain=[moid_min, moid_max])),
          y=alt.Y('cy:Q', scale=alt.Scale(domain=[p_min,    p_max])),
          text='label:N'
      )
)

right_points = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .mark_point(filled=True, stroke='white', strokeWidth=0.3)
      .encode(
          x=alt.X('MOID (AU):Q',
                  scale=alt.Scale(domain=[moid_min, moid_max]),
                  axis=alt.Axis(title='Earth Distance (MOID, AU) — smaller is closer', grid=True)),
          y=alt.Y('P (yr):Q',
                  scale=alt.Scale(domain=[p_min, p_max]),
                  axis=alt.Axis(title='Orbital Period (yrs)', grid=True)),
          color=alt.condition(
              brush, 'e:Q', alt.value('lightgray'),
              scale=alt.Scale(scheme='viridis'), title='Eccentricity'
          ),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('q (AU):Q',    title='Perihelion (AU)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
              alt.Tooltip('Decade:N',    title='Decade'),
          ]
      )
      .properties(width=SCATTER_W, height=SCATTER_H, title='MOID vs Orbital Period')
)

right = alt.layer(quad_rects, right_points, quad_labels)

right_caption_lines = [
    "What this shows: MOID vs return frequency (period).",
    "Why it matters: Smaller MOID → closer Earth-orbit intersections; short period → more often.",
    "Interpretation: Low MOID + short period → higher monitoring interest."
]
right_caption = caption_block(right_caption_lines, width=SCATTER_W, line_height=CAPTION_LINE_H)
right_block = alt.concat(right, right_caption, columns=1, spacing=6)

# -----------------------------
# TOP ROW
# -----------------------------
top_row = (left_block | right_block).resolve_scale(color='shared').properties(spacing=TOP_SPACING)

# -----------------------------
# Watchlist (labels wrapped; narrower width kept)
# -----------------------------
# -----------------------------
# Watchlist (labels wrapped; narrower width kept) — INVERTED PRIORITY
# -----------------------------
bars_caption_lines = [
    "What this shows: Screening metric combining proximity (1/MOID) and frequency (1/Period).",
    "Why it matters: Creates an actionable shortlist for monitoring.",
    "Note: Not a risk probability—size, inclination, uncertainties matter."
]

bars = (
    alt.Chart(df)
      .add_params(decade_select)
      .transform_filter((decade_select == 'All') | (alt.datum.Decade == decade_select))
      .transform_filter(brush)
      .transform_calculate(
          # wrap long names at whitespace after ~18 chars
          label_wrap="replace(datum['full_name'], /(.{18,}?)(\\s)/g, '$1\\n')",
          p_num   ="toNumber(datum['P (yr)'])",
          moid_num="toNumber(datum['MOID (AU)'])"
      )
      # keep only finite, positive values we can rank
      .transform_filter("isFinite(datum.p_num) && datum.p_num > 0 && isFinite(datum.moid_num) && datum.moid_num > 0")
      # normalize RAW P and RAW MOID, then invert so smaller = larger score
      .transform_joinaggregate(
          p_min='min(p_num)', p_max='max(p_num)',
          moid_min='min(moid_num)', moid_max='max(moid_num)'
      )
      .transform_calculate(
          p_norm   ="(datum.p_max   > datum.p_min)   ? (datum.p_num   - datum.p_min)   / (datum.p_max   - datum.p_min)   : 0",
          moid_norm="(datum.moid_max> datum.moid_min)? (datum.moid_num- datum.moid_min)/ (datum.moid_max- datum.moid_min): 0",
          # invert the scales so lower P / lower MOID -> higher component score
          freq_norm="1 - datum.p_norm",
          prox_norm="1 - datum.moid_norm",
          priority ="0.5 * (datum.freq_norm + datum.prox_norm)"
      )
      .transform_window(rank='rank()', sort=[alt.SortField('priority', order='descending')])
      .transform_filter(alt.datum.rank <= 10)
      .mark_bar()
      .encode(
          y=alt.Y('label_wrap:N',
                  sort='-x',
                  title='Top 10 Priority (current view/selection)',
                  axis=alt.Axis(labelLimit=280, labelPadding=4)),
          x=alt.X('priority:Q', title='Priority Score (higher = closer & more frequent)'),
          color=alt.Color('e:Q', title='Eccentricity', scale=alt.Scale(scheme='viridis')),
          tooltip=[
              alt.Tooltip('full_name:N', title='Object'),
              alt.Tooltip('priority:Q',  title='Priority Score', format='.3f'),
              alt.Tooltip('MOID (AU):Q', title='MOID (AU)'),
              alt.Tooltip('P (yr):Q',    title='Period (yrs)'),
              alt.Tooltip('e:Q',         title='Eccentricity'),
          ]
      )
      .properties(width=BARS_W, height=BARS_H, title='Watchlist: Top 10 by Priority (closer & more frequent)')
)

bars_caption = caption_block(bars_caption_lines, width=BARS_W, line_height=CAPTION_LINE_H)
bars_block  = alt.concat(bars,  bars_caption,  columns=1, spacing=6)

# --- Sidebar glossary textbox (drop-in) ---
# Width of the sidebar panel
SIDEBAR_W = 260

# Small title
glossary_title = (
    alt.Chart(pd.DataFrame({"text": ["Glossary"]}))
      .mark_text(align="left", baseline="top", fontSize=14, fontWeight="bold", color="#222")
      .encode(x=alt.value(0), y=alt.value(0), text="text:N")
      .properties(width=SIDEBAR_W, height=18)
)

# Bullet-style lines (kept short so they don't wrap awkwardly)
glossary_lines = [
    "• Eccentricity (e): 0 = circle; →1 = elongated ellipse.",
    "• Perihelion (q): Closest distance to the Sun (AU).",
    "• MOID: Min. orbit intersection distance w/ Earth (AU). Smaller = closer.",
    "• Orbital Period (P): Years per orbit. Shorter = more frequent returns.",
    "• AU: Astronomical Unit ≈ 149.6 million km."
]

glossary_block = alt.concat(
    glossary_title,
    caption_block(glossary_lines, width=SIDEBAR_W, line_height=CAPTION_LINE_H, fontsize=12),
    columns=1,
    spacing=6
).properties(width=SIDEBAR_W)

# -----------------------------
# FINAL
# -----------------------------

# ---- Top row (horizontal) ----
top_row = alt.concat(
    left_block,
    right_block,
    glossary_block,
    columns=3,
    spacing=TOP_SPACING
).resolve_scale(color='shared')

# 3) Final layout: stack top_row over bars
final = alt.concat(
    top_row,
    bars_block,
    columns=1,   # vertical stack
    spacing=18
).configure_axis(
    labelFontSize=10, titleFontSize=12
).configure_legend(
    labelFontSize=10, titleFontSize=12
).configure_view(
    stroke=None
)

final


SchemaValidationError: `ConcatChart` has no parameter named 'columns'

Existing parameter names are:
concat       bounds    data          padding   title       
align        center    datasets      params    transform   
autosize     columns   description   resolve   usermeta    
background   config    name          spacing               

See the help for `ConcatChart` to read the full description of these parameters

alt.ConcatChart(...)